In [5]:
#import necessary libraries
import pandas as pd
import numpy as np
import requests
import tweepy
import json
import matplotlib.pyplot as plt
%matplotlib inline
from timeit import default_timer as timer
from tweepy import OAuthHandler

In [6]:
pd.set_option('display.max_colwidth', -1)

# Gathering Data for this Project

In [7]:
# 1_read twitter_archive_enhanced.csv file
twitter_archive=pd.read_csv('twitter-archive-enhanced.csv')

In [8]:
twitter_archive.head()

tweet_id  in_reply_to_status_id  in_reply_to_user_id  \
0  892420643555336193 NaN                    NaN                    
1  892177421306343426 NaN                    NaN                    
2  891815181378084864 NaN                    NaN                    
3  891689557279858688 NaN                    NaN                    
4  891327558926688256 NaN                    NaN                    

                   timestamp  \
0  2017-08-01 16:23:56 +0000   
1  2017-08-01 00:17:27 +0000   
2  2017-07-31 00:18:03 +0000   
3  2017-07-30 15:58:51 +0000   
4  2017-07-29 16:00:24 +0000   

                                                                               source  \
0  <a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>   
1  <a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>   
2  <a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>   
3  <a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>   
4  <a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>   

                                                                                                                                                                 text  \
0  This is Phineas. He's a mystical boy. Only ever appears in the hole of a donut. 13/10 https://t.co/MgUWQ76dJU                                                        
1  This is Tilly. She's just checking pup on you. Hopes you're doing ok. If not, she's available for pats, snugs, boops, the whole bit. 13/10 https://t.co/0Xxu71qeIV   
2  This is Archie. He is a rare Norwegian Pouncing Corgo. Lives in the tall grass. You never know when one may strike. 12/10 https://t.co/wUnZnhtVJB                    
3  This is Darla. She commenced a snooze mid meal. 13/10 happens to the best of us https://t.co/tD36da7qLQ                                                              
4  This is Franklin. He would like you to stop calling him "cute." He is a very fierce shark and should be respected as such. 12/10 #BarkWeek https://t.co/AtUZn91f7f   

   retweeted_status_id  retweeted_status_user_id retweeted_status_timestamp  \
0 NaN                  NaN                        NaN                         
1 NaN                  NaN                        NaN                         
2 NaN                  NaN                        NaN                         
3 NaN                  NaN                        NaN                         
4 NaN                  NaN                        NaN                         

                                                                                                                     expanded_urls  \
0  https://twitter.com/dog_rates/status/892420643555336193/photo/1                                                                   
1  https://twitter.com/dog_rates/status/892177421306343426/photo/1                                                                   
2  https://twitter.com/dog_rates/status/891815181378084864/photo/1                                                                   
3  https://twitter.com/dog_rates/status/891689557279858688/photo/1                                                                   
4  https://twitter.com/dog_rates/status/891327558926688256/photo/1,https://twitter.com/dog_rates/status/891327558926688256/photo/1   

   rating_numerator  rating_denominator      name doggo floofer pupper puppo  
0  13                10                  Phineas   None  None    None   None  
1  13                10                  Tilly     None  None    None   None  
2  12                10                  Archie    None  None    None   None  
3  13                10                  Darla     None  None    None   None  
4  12                10                  Franklin  None  None    None   None

In [9]:
twitter_archive.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2356 entries, 0 to 2355
Data columns (total 17 columns):
tweet_id                      2356 non-null int64
in_reply_to_status_id         78 non-null float64
in_reply_to_user_id           78 non-null float64
timestamp                     2356 non-null object
source                        2356 non-null object
text                          2356 non-null object
retweeted_status_id           181 non-null float64
retweeted_status_user_id      181 non-null float64
retweeted_status_timestamp    181 non-null object
expanded_urls                 2297 non-null object
rating_numerator              2356 non-null int64
rating_denominator            2356 non-null int64
name                          2356 non-null object
doggo                         2356 non-null object
floofer                       2356 non-null object
pupper                        2356 non-null object
puppo                         2356 non-null object
dtypes: float64(4), int64(3), ob

In [10]:
#2_downloaded programmatically the file (image_predictions.tsv) which is hosted on Udacity's servers:

url='https://d17h27t6h515a5.cloudfront.net/topher/2017/August/599fd2ad_image-predictions/image-predictions.tsv'
r=requests.get(url)

with open('image-predictions.tsv', 'wb') as f:
    f.write(r.content)
    
image_predictions= pd.read_csv('image-predictions.tsv', sep='\t')

In [11]:
image_predictions.head()

tweet_id                                          jpg_url  \
0  666020888022790149  https://pbs.twimg.com/media/CT4udn0WwAA0aMy.jpg   
1  666029285002620928  https://pbs.twimg.com/media/CT42GRgUYAA5iDo.jpg   
2  666033412701032449  https://pbs.twimg.com/media/CT4521TWwAEvMyu.jpg   
3  666044226329800704  https://pbs.twimg.com/media/CT5Dr8HUEAA-lEu.jpg   
4  666049248165822465  https://pbs.twimg.com/media/CT5IQmsXIAAKY4A.jpg   

   img_num                      p1   p1_conf  p1_dog                  p2  \
0  1        Welsh_springer_spaniel  0.465074  True    collie               
1  1        redbone                 0.506826  True    miniature_pinscher   
2  1        German_shepherd         0.596461  True    malinois             
3  1        Rhodesian_ridgeback     0.408143  True    redbone              
4  1        miniature_pinscher      0.560311  True    Rottweiler           

    p2_conf  p2_dog                   p3   p3_conf  p3_dog  
0  0.156665  True    Shetland_sheepdog    0.061428  True    
1  0.074192  True    Rhodesian_ridgeback  0.072010  True    
2  0.138584  True    bloodhound           0.116197  True    
3  0.360687  True    miniature_pinscher   0.222752  True    
4  0.243682  True    Doberman             0.154629  True

In [8]:
image_predictions.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2075 entries, 0 to 2074
Data columns (total 12 columns):
tweet_id    2075 non-null int64
jpg_url     2075 non-null object
img_num     2075 non-null int64
p1          2075 non-null object
p1_conf     2075 non-null float64
p1_dog      2075 non-null bool
p2          2075 non-null object
p2_conf     2075 non-null float64
p2_dog      2075 non-null bool
p3          2075 non-null object
p3_conf     2075 non-null float64
p3_dog      2075 non-null bool
dtypes: bool(3), float64(3), int64(2), object(4)
memory usage: 152.1+ KB


In [45]:
# Create Tweepy API object
consumer_key = 'aaa'
consumer_secret = 'aaa'
access_token = 'aaa'
access_secret = 'aaa'



auth = tweepy.OAuthHandler(consumer_key, consumer_secret)
auth.set_access_token(access_token, access_secret)

api = tweepy.API(auth,parser=tweepy.parsers.JSONParser(), wait_on_rate_limit=True, wait_on_rate_limit_notify=True)

In [47]:
#3_Query Twitter's API for JSON data for each tweet ID in the Twitter archive


tweet_id_list=list(twitter_archive.tweet_id.values)
count = 0
start = timer()
fail_tweets= []
success_tweets=[]
data_tweets=[]

for tweet_id in tweet_id_list:
    count += 1
    print(str(count) + ": " + str(tweet_id)) #Hamza: I commented this
    
    #hamza Added these lines for test: start
    #it will run limited number of lines
    #if count > 20:
    #       break
    #Hamza: end
    
    try:
        tweet = api.get_status(tweet_id, tweet_mode='extended')
        data_tweets.append(tweet) 
        success_tweets.append(tweet_id)
        print("Success")
    except :
        print("Fail") #Hamza: I commented this
        fail_tweets.append(tweet_id)
        
            
end = timer()
print(end - start)
print(fail_tweets) #Hamza: I commented this
print(len(fail_tweets)) #Hamza: Added this: 
                        #it will print the nuber of fails

#Hamza: I stopped the printing. Except when success
#and the end will get the how many failed
#compare number of fails to the if count breal limit

1: 892420643555336193
Success
2: 892177421306343426
Success
3: 891815181378084864
Success
4: 891689557279858688
Success
5: 891327558926688256
Success
6: 891087950875897856
Success
7: 890971913173991426
Success
8: 890729181411237888
Success
9: 890609185150312448
Success
10: 890240255349198849
Success
11: 890006608113172480
Success
12: 889880896479866881
Success
13: 889665388333682689
Success
14: 889638837579907072
Success
15: 889531135344209921
Success
16: 889278841981685760
Success
17: 888917238123831296
Success
18: 888804989199671297
Success
19: 888554962724278272
Success
20: 888202515573088257
Fail
21: 888078434458587136
Success
22: 887705289381826560
Success
23: 887517139158093824
Success
24: 887473957103951883
Success
25: 887343217045368832
Success
26: 887101392804085760
Success
27: 886983233522544640
Success
28: 886736880519319552
Success
29: 886680336477933568
Success
30: 886366144734445568
Success
31: 886267009285017600
Success
32: 886258384151887873
Success
33: 8860541600590725

Success
263: 842765311967449089
Success
264: 842535590457499648
Success
265: 842163532590374912
Success
266: 842115215311396866
Success
267: 841833993020538882
Success
268: 841680585030541313
Success
269: 841439858740625411
Success
270: 841320156043304961
Success
271: 841314665196081154
Success
272: 841077006473256960
Success
273: 840761248237133825
Success
274: 840728873075638272
Success
275: 840698636975636481
Success
276: 840696689258311684
Success
277: 840632337062862849
Success
278: 840370681858686976
Success
279: 840268004936019968
Success
280: 839990271299457024
Success
281: 839549326359670784
Success
282: 839290600511926273
Success
283: 839239871831150596
Success
284: 838952994649550848
Success
285: 838921590096166913
Success
286: 838916489579200512
Success
287: 838831947270979586
Success
288: 838561493054533637
Success
289: 838476387338051585
Success
290: 838201503651401729
Success
291: 838150277551247360
Success
292: 838085839343206401
Success
293: 838083903487373313
Success


Success
520: 810284430598270976
Success
521: 810254108431155201
Success
522: 809920764300447744
Success
523: 809808892968534016
Success
524: 809448704142938112
Success
525: 809220051211603969
Success
526: 809084759137812480
Success
527: 808838249661788160
Success
528: 808733504066486276
Success
529: 808501579447930884
Success
530: 808344865868283904
Success
531: 808134635716833280
Success
532: 808106460588765185
Success
533: 808001312164028416
Success
534: 807621403335917568
Success
535: 807106840509214720
Success
536: 807059379405148160
Success
537: 807010152071229440
Success
538: 806629075125202948
Success
539: 806620845233815552
Success
540: 806576416489959424
Success
541: 806542213899489280
Success
542: 806242860592926720
Success
543: 806219024703037440
Success
544: 805958939288408065
Success
545: 805932879469572096
Success
546: 805826884734976000
Success
547: 805823200554876929
Success
548: 805520635690676224
Success
549: 805487436403003392
Success
550: 805207613751304193
Success


Success
776: 776201521193218049
Success
777: 776113305656188928
Success
778: 776088319444877312
Success
779: 775898661951791106
Success
780: 775842724423557120
Success
781: 775733305207554048
Success
782: 775729183532220416
Success
783: 775364825476165632
Success
784: 775350846108426240
Success
785: 775096608509886464
Fail
786: 775085132600442880
Success
787: 774757898236878852
Success
788: 774639387460112384
Success
789: 774314403806253056
Success
790: 773985732834758656
Success
791: 773922284943896577
Success
792: 773704687002451968
Success
793: 773670353721753600
Success
794: 773547596996571136
Success
795: 773336787167145985
Success
796: 773308824254029826
Success
797: 773247561583001600
Success
798: 773191612633579521
Success
799: 772877495989305348
Success
800: 772826264096874500
Success
801: 772615324260794368
Success
802: 772581559778025472
Success
803: 772193107915964416
Success
804: 772152991789019136
Success
805: 772117678702071809
Success
806: 772114945936949249
Success
807

Success
1033: 745314880350101504
Success
1034: 745074613265149952
Success
1035: 745057283344719872
Success
1036: 744995568523612160
Success
1037: 744971049620602880
Success
1038: 744709971296780288
Success
1039: 744334592493166593
Success
1040: 744234799360020481
Success
1041: 744223424764059648
Success
1042: 743980027717509120
Success
1043: 743895849529389061
Success
1044: 743835915802583040
Success
1045: 743609206067040256
Success
1046: 743595368194129920
Success
1047: 743545585370791937
Success
1048: 743510151680958465
Success
1049: 743253157753532416
Success
1050: 743222593470234624
Success
1051: 743210557239623680
Success
1052: 742534281772302336
Success
1053: 742528092657332225
Success
1054: 742465774154047488
Success
1055: 742423170473463808
Success
1056: 742385895052087300
Success
1057: 742161199639494656
Success
1058: 742150209887731712
Success
1059: 741793263812808706
Success
1060: 741743634094141440
Success
1061: 741438259667034112
Success
1062: 741303864243200000
Success
10

Success
1283: 708738143638450176
Success
1284: 708711088997666817
Success
1285: 708479650088034305
Success
1286: 708469915515297792
Success
1287: 708400866336894977
Success
1288: 708356463048204288
Success
1289: 708349470027751425
Success
1290: 708149363256774660
Success
1291: 708130923141795840
Success
1292: 708119489313951744
Success
1293: 708109389455101952
Success
1294: 708026248782585858
Success
1295: 707995814724026368
Success
1296: 707983188426153984
Success
1297: 707969809498152960
Success
1298: 707776935007539200
Success
1299: 707741517457260545
Success
1300: 707738799544082433
Success
1301: 707693576495472641
Success
1302: 707629649552134146
Success
1303: 707610948723478529
Success
1304: 707420581654872064
Success
1305: 707411934438625280
Success
1306: 707387676719185920
Success
1307: 707377100785885184
Success
1308: 707315916783140866
Success
1309: 707297311098011648
Success
1310: 707059547140169728
Success
1311: 707038192327901184
Success
1312: 707021089608753152
Success
13

Success
1532: 690015576308211712
Success
1533: 690005060500217858
Success
1534: 689999384604450816
Success
1535: 689993469801164801
Success
1536: 689977555533848577
Success
1537: 689905486972461056
Success
1538: 689877686181715968
Success
1539: 689835978131935233
Success
1540: 689661964914655233
Success
1541: 689659372465688576
Success
1542: 689623661272240129
Success
1543: 689599056876867584
Success
1544: 689557536375177216
Success
1545: 689517482558820352
Success
1546: 689289219123089408
Success
1547: 689283819090870273
Success
1548: 689280876073582592
Success
1549: 689275259254616065
Success
1550: 689255633275777024
Success
1551: 689154315265683456
Success
1552: 689143371370250240
Success
1553: 688916208532455424
Success
1554: 688908934925697024
Success
1555: 688898160958271489
Success
1556: 688894073864884227
Success
1557: 688828561667567616
Success
1558: 688804835492233216
Success
1559: 688789766343622656
Success
1560: 688547210804498433
Success
1561: 688519176466644993
Success
15

Success
1781: 677700003327029250
Success
1782: 677698403548192770
Success
1783: 677687604918272002
Success
1784: 677673981332312066
Success
1785: 677662372920729601
Success
1786: 677644091929329666
Success
1787: 677573743309385728
Success
1788: 677565715327688705
Success
1789: 677557565589463040
Success
1790: 677547928504967168
Success
1791: 677530072887205888
Success
1792: 677335745548390400
Success
1793: 677334615166730240
Success
1794: 677331501395156992
Success
1795: 677328882937298944
Success
1796: 677314812125323265
Success
1797: 677301033169788928
Success
1798: 677269281705472000
Success
1799: 677228873407442944
Success
1800: 677187300187611136
Success
1801: 676975532580409345
Success
1802: 676957860086095872
Success
1803: 676949632774234114
Success
1804: 676948236477857792
Success
1805: 676946864479084545
Success
1806: 676942428000112642
Success
1807: 676936541936185344
Success
1808: 676916996760600576
Success
1809: 676897532954456065
Success
1810: 676864501615042560
Success
18

Success
2031: 671789708968640512
Success
2032: 671768281401958400
Success
2033: 671763349865160704
Success
2034: 671744970634719232
Success
2035: 671743150407421952
Success
2036: 671735591348891648
Success
2037: 671729906628341761
Success
2038: 671561002136281088
Success
2039: 671550332464455680
Success
2040: 671547767500775424
Success
2041: 671544874165002241
Success
2042: 671542985629241344
Success
2043: 671538301157904385
Success
2044: 671536543010570240
Success
2045: 671533943490011136
Success
2046: 671528761649688577
Success
2047: 671520732782923777
Success
2048: 671518598289059840
Success
2049: 671511350426865664
Success
2050: 671504605491109889
Success
2051: 671497587707535361
Success
2052: 671488513339211776
Success
2053: 671486386088865792
Success
2054: 671485057807351808
Success
2055: 671390180817915904
Success
2056: 671362598324076544
Success
2057: 671357843010908160
Success
2058: 671355857343524864
Success
2059: 671347597085433856
Success
2060: 671186162933985280
Success
20

Success
2281: 667393430834667520
Success
2282: 667369227918143488
Success
2283: 667211855547486208
Success
2284: 667200525029539841
Success
2285: 667192066997374976
Success
2286: 667188689915760640
Success
2287: 667182792070062081
Success
2288: 667177989038297088
Success
2289: 667176164155375616
Success
2290: 667174963120574464
Success
2291: 667171260800061440
Success
2292: 667165590075940865
Success
2293: 667160273090932737
Success
2294: 667152164079423490
Success
2295: 667138269671505920
Success
2296: 667119796878725120
Success
2297: 667090893657276420
Success
2298: 667073648344346624
Success
2299: 667070482143944705
Success
2300: 667065535570550784
Success
2301: 667062181243039745
Success
2302: 667044094246576128
Success
2303: 667012601033924608
Success
2304: 666996132027977728
Success
2305: 666983947667116034
Success
2306: 666837028449972224
Success
2307: 666835007768551424
Success
2308: 666826780179869698
Success
2309: 666817836334096384
Success
2310: 666804364988780544
Success
23

In [48]:
with open('tweet_json.txt', mode = 'w') as file:
    json.dump(data_tweets, file)

In [49]:
data_tweets

[{'created_at': 'Tue Aug 01 16:23:56 +0000 2017',
  'id': 892420643555336193,
  'id_str': '892420643555336193',
  'full_text': "This is Phineas. He's a mystical boy. Only ever appears in the hole of a donut. 13/10 https://t.co/MgUWQ76dJU",
  'truncated': False,
  'display_text_range': [0, 85],
  'entities': {'hashtags': [],
   'symbols': [],
   'user_mentions': [],
   'urls': [],
   'media': [{'id': 892420639486877696,
     'id_str': '892420639486877696',
     'indices': [86, 109],
     'media_url': 'http://pbs.twimg.com/media/DGKD1-bXoAAIAUK.jpg',
     'media_url_https': 'https://pbs.twimg.com/media/DGKD1-bXoAAIAUK.jpg',
     'url': 'https://t.co/MgUWQ76dJU',
     'display_url': 'pic.twitter.com/MgUWQ76dJU',
     'expanded_url': 'https://twitter.com/dog_rates/status/892420643555336193/photo/1',
     'type': 'photo',
     'sizes': {'thumb': {'w': 150, 'h': 150, 'resize': 'crop'},
      'medium': {'w': 540, 'h': 528, 'resize': 'fit'},
      'small': {'w': 540, 'h': 528, 'resize': 'fit'}

In [12]:
# read this tweet_json.txt file line by line into a pandas DataFrame with tweet_id, retweet_count
#, and favorites_count and followers_count

tweets_data = []
with open('tweet_json.txt', encoding='utf-8') as json_file:  
    data = json.load(json_file)
    
    for tweet in data:
        tweet_id = tweet['id']
        followers_count = tweet['user']['followers_count']
        favourites_count = tweet['user']['favourites_count']
        retweet_count = tweet['retweet_count']
        tweets_data.append({'tweet_id': str(tweet_id),
                            'followers_count': int(followers_count),
                            'favourites_count': int(favourites_count),
                            'retweet_count': int(retweet_count)
                            })
        
tweet_json = pd.DataFrame(tweets_data, columns = ['tweet_id', 'followers_count','favourites_count'
                                                          ,'retweet_count'])

In [13]:
tweet_json.head()

tweet_id  followers_count  favourites_count  retweet_count
0  892420643555336193  8848624          145964            7561         
1  892177421306343426  8848624          145964            5603         
2  891815181378084864  8848625          145964            3713         
3  891689557279858688  8848625          145964            7745         
4  891327558926688256  8848625          145964            8339

# Assessing Data

Assess data visually and programmatically for quality and tidiness issues. Detect and document at least eight (8) quality issues and two (2) tidiness issues in your wrangle_act.ipynb Jupyter Notebook. To meet specifications, the issues that satisfy the Project Motivation (see the Key Points header on the previous page) must be assessed.

### Visual and programmatical assessment: <br>
Each dataset is displayed for visual assessment and then tested with pandas functions:

In [14]:
# 1- twitter_archive assessement:
twitter_archive


tweet_id  in_reply_to_status_id  in_reply_to_user_id  \
0     892420643555336193 NaN                    NaN                    
1     892177421306343426 NaN                    NaN                    
2     891815181378084864 NaN                    NaN                    
3     891689557279858688 NaN                    NaN                    
4     891327558926688256 NaN                    NaN                    
5     891087950875897856 NaN                    NaN                    
6     890971913173991426 NaN                    NaN                    
7     890729181411237888 NaN                    NaN                    
8     890609185150312448 NaN                    NaN                    
9     890240255349198849 NaN                    NaN                    
10    890006608113172480 NaN                    NaN                    
11    889880896479866881 NaN                    NaN                    
12    889665388333682689 NaN                    NaN                    
13    889638837579907072 NaN                    NaN                    
14    889531135344209921 NaN                    NaN                    
15    889278841981685760 NaN                    NaN                    
16    888917238123831296 NaN                    NaN                    
17    888804989199671297 NaN                    NaN                    
18    888554962724278272 NaN                    NaN                    
19    888202515573088257 NaN                    NaN                    
20    888078434458587136 NaN                    NaN                    
21    887705289381826560 NaN                    NaN                    
22    887517139158093824 NaN                    NaN                    
23    887473957103951883 NaN                    NaN                    
24    887343217045368832 NaN                    NaN                    
25    887101392804085760 NaN                    NaN                    
26    886983233522544640 NaN                    NaN                    
27    886736880519319552 NaN                    NaN                    
28    886680336477933568 NaN                    NaN                    
29    886366144734445568 NaN                    NaN                    
...                  ...  ..                     ..                    
2326  666411507551481857 NaN                    NaN                    
2327  666407126856765440 NaN                    NaN                    
2328  666396247373291520 NaN                    NaN                    
2329  666373753744588802 NaN                    NaN                    
2330  666362758909284353 NaN                    NaN                    
2331  666353288456101888 NaN                    NaN                    
2332  666345417576210432 NaN                    NaN                    
2333  666337882303524864 NaN                    NaN                    
2334  666293911632134144 NaN                    NaN                    
2335  666287406224695296 NaN                    NaN                    
2336  666273097616637952 NaN                    NaN                    
2337  666268910803644416 NaN                    NaN                    
2338  666104133288665088 NaN                    NaN                    
2339  666102155909144576 NaN                    NaN                    
2340  666099513787052032 NaN                    NaN                    
2341  666094000022159362 NaN                    NaN                    
2342  666082916733198337 NaN                    NaN                    
2343  666073100786774016 NaN                    NaN                    
2344  666071193221509120 NaN                    NaN                    
2345  666063827256086533 NaN                    NaN                    
2346  666058600524156928 NaN                    NaN                    
2347  666057090499244032 NaN                    NaN                    
2348  666055525042405380 NaN                    NaN                    
2349  666051853826850816 NaN                    NaN     

In [15]:
twitter_archive.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2356 entries, 0 to 2355
Data columns (total 17 columns):
tweet_id                      2356 non-null int64
in_reply_to_status_id         78 non-null float64
in_reply_to_user_id           78 non-null float64
timestamp                     2356 non-null object
source                        2356 non-null object
text                          2356 non-null object
retweeted_status_id           181 non-null float64
retweeted_status_user_id      181 non-null float64
retweeted_status_timestamp    181 non-null object
expanded_urls                 2297 non-null object
rating_numerator              2356 non-null int64
rating_denominator            2356 non-null int64
name                          2356 non-null object
doggo                         2356 non-null object
floofer                       2356 non-null object
pupper                        2356 non-null object
puppo                         2356 non-null object
dtypes: float64(4), int64(3), ob

In [16]:
#check if there is any duplication in the data set
sum(twitter_archive.duplicated())

0

In [17]:
#check if there is any duplication in the tweets id
sum(twitter_archive.text.duplicated())

0

In [18]:
twitter_archive.name.value_counts()

None            745
a               55 
Charlie         12 
Lucy            11 
Oliver          11 
Cooper          11 
Tucker          10 
Lola            10 
Penny           10 
Winston         9  
Bo              9  
the             8  
Sadie           8  
Buddy           7  
Daisy           7  
Bailey          7  
an              7  
Toby            7  
Stanley         6  
Jax             6  
Dave            6  
Milo            6  
Koda            6  
Scout           6  
Oscar           6  
Rusty           6  
Leo             6  
Jack            6  
Bella           6  
very            5  
               ..  
Ralpher         1  
Hazel           1  
Enchilada       1  
Halo            1  
Liam            1  
Bonaparte       1  
Clybe           1  
Ronduh          1  
Sephie          1  
Zooey           1  
Rinna           1  
Jimbo           1  
Willy           1  
O               1  
Jameson         1  
Alexanderson    1  
Callie          1  
Ralphson        1  
Dallas          1  


In [19]:

np.sort(twitter_archive.name.unique())

array(['Abby', 'Ace', 'Acro', 'Adele', 'Aiden', 'Aja', 'Akumi', 'Al',
       'Albert', 'Albus', 'Aldrick', 'Alejandro', 'Alexander',
       'Alexanderson', 'Alf', 'Alfie', 'Alfy', 'Alice', 'Amber', 'Ambrose',
       'Amy', 'Amélie', 'Anakin', 'Andru', 'Andy', 'Angel', 'Anna',
       'Anthony', 'Antony', 'Apollo', 'Aqua', 'Archie', 'Arlen', 'Arlo',
       'Arnie', 'Arnold', 'Arya', 'Ash', 'Asher', 'Ashleigh', 'Aspen',
       'Astrid', 'Atlas', 'Atticus', 'Aubie', 'Augie', 'Autumn', 'Ava',
       'Axel', 'Bailey', 'Baloo', 'Balto', 'Banditt', 'Banjo', 'Barclay',
       'Barney', 'Baron', 'Barry', 'Batdog', 'Bauer', 'Baxter', 'Bayley',
       'BeBe', 'Bear', 'Beau', 'Beckham', 'Beebop', 'Beemo', 'Bell',
       'Bella', 'Belle', 'Ben', 'Benedict', 'Benji', 'Benny', 'Bentley',
       'Berb', 'Berkeley', 'Bernie', 'Bert', 'Bertson', 'Betty', 'Beya',
       'Biden', 'Bilbo', 'Billl', 'Billy', 'Binky', 'Birf', 'Bisquick',
       'Blakely', 'Blanket', 'Blipson', 'Blitz', 'Bloo', 'Bloop', 'Blu',

In [20]:
twitter_archive.query('name == "Al"').text

820    Meet Al Cabone. He's a gangsta puppa. Rather h*ckin ruthless. Shows no mercy sometimes. 11/10 pet w extreme caution https://t.co/OUwWbEKOUV
Name: text, dtype: object

In [21]:
twitter_archive.query('name == "O"').text

775    This is O'Malley. That is how he sleeps. Doesn't care what you think about it. 10/10 comfy af https://t.co/Pq150LeRaC
Name: text, dtype: object

In [22]:
twitter_archive.query("name == ['a', 'actually', 'all', 'an', 'by', 'getting', 'his','incredibly','infuriating','just','life','light','mad','my','not','officially','old','one','quite','space','such','the','this','unacceptable','very']").text

22      I've yet to rate a Venezuelan Hover Wiener. This is such an honor. 14/10 paw-inspiring af (IG: roxy.thedoxy) https://t.co/20VrLAA8ba                              
56      Here is a pupper approaching maximum borkdrive. Zooming at never before seen speeds. 14/10 paw-inspiring af \n(IG: puffie_the_chow) https://t.co/ghXBIIeQZF       
118     RT @dog_rates: We only rate dogs. This is quite clearly a smol broken polar bear. We'd appreciate if you only send dogs. Thank you... 12/10…                      
169     We only rate dogs. This is quite clearly a smol broken polar bear. We'd appreciate if you only send dogs. Thank you... 12/10 https://t.co/g2nSyGenG9              
193     Guys, we only rate dogs. This is quite clearly a bulbasaur. Please only send dogs. Thank you... 12/10 human used pet, it's super effective https://t.co/Xc7uj1C64x
335     There's going to be a dog terminal at JFK Airport. This is not a drill. 10/10  \nhttps://t.co/dp5h9bCwU7                                 

In [23]:
#chech the values in denominator
twitter_archive.rating_denominator.value_counts()

10     2333
11     3   
50     3   
80     2   
20     2   
2      1   
16     1   
40     1   
70     1   
15     1   
90     1   
110    1   
120    1   
130    1   
150    1   
170    1   
7      1   
0      1   
Name: rating_denominator, dtype: int64

In [24]:
twitter_archive.query('rating_denominator != 10').text

313     @jonnysun @Lin_Manuel ok jomny I know you're excited but 960/00 isn't a valid rating, 13/10 is tho                                                                       
342     @docmisterio account started on 11/15/15                                                                                                                                 
433     The floofs have been released I repeat the floofs have been released. 84/70 https://t.co/NIYC820tmd                                                                      
516     Meet Sam. She smiles 24/7 &amp; secretly aspires to be a reindeer. \nKeep Sam smiling by clicking and sharing this link:\nhttps://t.co/98tB8y7y7t https://t.co/LouL5vdvxx
784     RT @dog_rates: After so many requests, this is Bretagne. She was the last surviving 9/11 search dog, and our second ever 14/10. RIP https:/…                             
902     Why does this never happen at my front door... 165/150 https://t.co/HmwrdfEfUE                        

In [25]:
twitter_archive.query('rating_denominator == 0')

tweet_id  in_reply_to_status_id  in_reply_to_user_id  \
313  835246439529840640  8.352460e+17           26259576.0            

                     timestamp  \
313  2017-02-24 21:54:03 +0000   

                                                                                 source  \
313  <a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>   

                                                                                                   text  \
313  @jonnysun @Lin_Manuel ok jomny I know you're excited but 960/00 isn't a valid rating, 13/10 is tho   

     retweeted_status_id  retweeted_status_user_id retweeted_status_timestamp  \
313 NaN                  NaN                        NaN                         

    expanded_urls  rating_numerator  rating_denominator  name doggo floofer  \
313  NaN           960               0                   None  None  None     

    pupper puppo  
313  None   None

In [26]:
# Assissing image_predictions
image_predictions

tweet_id  \
0     666020888022790149   
1     666029285002620928   
2     666033412701032449   
3     666044226329800704   
4     666049248165822465   
5     666050758794694657   
6     666051853826850816   
7     666055525042405380   
8     666057090499244032   
9     666058600524156928   
10    666063827256086533   
11    666071193221509120   
12    666073100786774016   
13    666082916733198337   
14    666094000022159362   
15    666099513787052032   
16    666102155909144576   
17    666104133288665088   
18    666268910803644416   
19    666273097616637952   
20    666287406224695296   
21    666293911632134144   
22    666337882303524864   
23    666345417576210432   
24    666353288456101888   
25    666362758909284353   
26    666373753744588802   
27    666396247373291520   
28    666407126856765440   
29    666411507551481857   
...                  ...   
2045  886366144734445568   
2046  886680336477933568   
2047  886736880519319552   
2048  886983233522544640   
2049  887101392804085760   
2050  887343217045368832   
2051  887473957103951883   
2052  887517139158093824   
2053  887705289381826560   
2054  888078434458587136   
2055  888202515573088257   
2056  888554962724278272   
2057  888804989199671297   
2058  888917238123831296   
2059  889278841981685760   
2060  889531135344209921   
2061  889638837579907072   
2062  889665388333682689   
2063  889880896479866881   
2064  890006608113172480   
2065  890240255349198849   
2066  890609185150312448   
2067  890729181411237888   
2068  890971913173991426   
2069  891087950875897856   
2070  891327558926688256   
2071  891689557279858688   
2072  891815181378084864   
2073  892177421306343426   
2074  892420643555336193   

                                                                                      jpg_url  \
0     https://pbs.twimg.com/media/CT4udn0WwAA0aMy.jpg                                           
1     https://pbs.twimg.com/media/CT42GRgUYAA5iDo.jpg                                           
2     https://pbs.twimg.com/media/CT4521TWwAEvMyu.jpg                                           
3     https://pbs.twimg.com/media/CT5Dr8HUEAA-lEu.jpg                                           
4     https://pbs.twimg.com/media/CT5IQmsXIAAKY4A.jpg                                           
5     https://pbs.twimg.com/media/CT5Jof1WUAEuVxN.jpg                                           
6     https://pbs.twimg.com/media/CT5KoJ1WoAAJash.jpg                                           
7     https://pbs.twimg.com/media/CT5N9tpXIAAifs1.jpg                                           
8     https://pbs.twimg.com/media/CT5PY90WoAAQGLo.jpg                                           
9     https://pbs.twimg.com/media/CT5Qw94XAAA_2dP.jpg                                           
10    https://pbs.twimg.com/media/CT5Vg_wXIAAXfnj.jpg                                           
11    https://pbs.twimg.com/media/CT5cN_3WEAAlOoZ.jpg                                           
12    https://pbs.twimg.com/media/CT5d9DZXAAALcwe.jpg                                           
13    https://pbs.twimg.com/media/CT5m4VGWEAAtKc8.jpg                                           
14    https://pbs.twimg.com/media/CT5w9gUW4AAsBNN.jpg                                           
15    https://pbs.twimg.com/media/CT51-JJUEAA6hV8.jpg                                           
16    https://pbs.twimg.com/media/CT54YGiWUAEZnoK.jpg                                           
17    https://pbs.twimg.com/media/CT56LSZWoAAlJj2.jpg                                           
18    https://pbs.twimg.com/media/CT8QCd1WEAADXws.jpg                                           
19    https://pbs.twimg.com/media/CT8T1mtUwAA3aqm.jpg                                           
20    https://pbs.twimg.com/media/CT8g3BpUEAAuFjg.jpg                                           
21    https://pbs.twimg.com/media/CT8mx7KW4AEQu8N.jpg                                           
22    https://pbs.twimg.com/media/CT9OwFIWEAMuRj

In [27]:
image_predictions.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2075 entries, 0 to 2074
Data columns (total 12 columns):
tweet_id    2075 non-null int64
jpg_url     2075 non-null object
img_num     2075 non-null int64
p1          2075 non-null object
p1_conf     2075 non-null float64
p1_dog      2075 non-null bool
p2          2075 non-null object
p2_conf     2075 non-null float64
p2_dog      2075 non-null bool
p3          2075 non-null object
p3_conf     2075 non-null float64
p3_dog      2075 non-null bool
dtypes: bool(3), float64(3), int64(2), object(4)
memory usage: 152.1+ KB


In [28]:
#check if there is duplication
sum(image_predictions.duplicated())

0

In [29]:
sum(image_predictions.jpg_url.duplicated())

66

In [30]:
image_predictions[image_predictions.jpg_url.duplicated()]

tweet_id  \
1297  752309394570878976   
1315  754874841593970688   
1333  757729163776290825   
1345  759159934323924993   
1349  759566828574212096   
1364  761371037149827077   
1368  761750502866649088   
1387  766078092750233600   
1407  770093767776997377   
1417  771171053431250945   
1427  772615324260794368   
1446  775898661951791106   
1453  776819012571455488   
1456  777641927919427584   
1463  778396591732486144   
1476  780496263422808064   
1487  782021823840026624   
1495  783347506784731136   
1510  786036967502913536   
1522  788070120937619456   
1538  790723298204217344   
1541  791026214425268224   
1564  793614319594401792   
1569  794355576146903043   
1571  794983741416415232   
1579  796177847564038144   
1588  798340744599797760   
1589  798628517273620480   
1590  798644042770751489   
1591  798665375516884993   
...                  ...   
1619  802624713319034886   
1624  803692223237865472   
1627  804413760345620481   
1634  805958939288408065   
1636  806242860592926720   
1640  807059379405148160   
1645  808134635716833280   
1652  809808892968534016   
1683  813944609378369540   
1693  816014286006976512   
1699  816829038950027264   
1703  817181837579653120   
1712  818588835076603904   
1717  819015331746349057   
1718  819015337530290176   
1727  820446719150292993   
1736  821813639212650496   
1742  822647212903690241   
1746  823269594223824897   
1755  824796380199809024   
1789  829878982036299777   
1803  832040443403784192   
1804  832215726631055365   
1858  841833993020538882   
1864  842892208864923648   
1903  851953902622658560   
1944  861769973181624320   
1992  873697596434513921   
2041  885311592912609280   
2055  888202515573088257   

                                                                                      jpg_url  \
1297  https://pbs.twimg.com/ext_tw_video_thumb/675354114423808004/pu/img/qL1R_nGLqa6lmkOx.jpg   
1315  https://pbs.twimg.com/media/CWza7kpWcAAdYLc.jpg                                           
1333  https://pbs.twimg.com/media/CWyD2HGUYAQ1Xa7.jpg                                           
1345  https://pbs.twimg.com/media/CU1zsMSUAAAS0qW.jpg                                           
1349  https://pbs.twimg.com/media/CkNjahBXAAQ2kWo.jpg                                           
1364  https://pbs.twimg.com/tweet_video_thumb/CeBym7oXEAEWbEg.jpg                               
1368  https://pbs.twimg.com/media/CYLDikFWEAAIy1y.jpg                                           
1387  https://pbs.twimg.com/media/ChK1tdBWwAQ1flD.jpg                                           
1407  https://pbs.twimg.com/media/CkjMx99UoAM2B1a.jpg                                           
1417  https://pbs.twimg.com/media/CVgdFjNWEAAxmbq.jpg                                           
1427  https://pbs.twimg.com/media/Cp6db4-XYAAMmqL.jpg                                           
1446  https://pbs.twimg.com/media/CiyHLocU4AI2pJu.jpg                                           
1453  https://pbs.twimg.com/media/CW88XN4WsAAlo8r.jpg                                           
1456  https://pbs.twimg.com/media/CmoPdmHW8AAi8BI.jpg                                           
1463  https://pbs.twimg.com/media/CcG07BYW0AErrC9.jpg                                           
1476  https://pbs.twimg.com/media/Ck2d7tJWUAEPTL3.jpg                                           
1487  https://pbs.twimg.com/media/CdHwZd0VIAA4792.jpg                                           
1495  https://pbs.twimg.com/media/CVuQ2LeUsAAIe3s.jpg                                           
1510  https://pbs.twimg.com/media/CtKHLuCWYAA2TTs.jpg                                           
1522  https://pbs.twimg.com/media/Co-hmcYXYAASkiG.jpg                                           
1538  https://pbs.twimg.com/media/CvaYgDOWgAEfjls.jpg                                           
1541  https://pbs.twimg.com/media/CpmyNumW8AAAJGj.jpg                                           
1564  https://pbs.twimg.com/media/CvyVxQRWEAAdSZ

In [31]:
image_predictions[image_predictions.jpg_url== "https://pbs.twimg.com/media/CzG425nWgAAnP7P.jpg"]

tweet_id                                          jpg_url  \
1638  806629075125202948  https://pbs.twimg.com/media/CzG425nWgAAnP7P.jpg   
1944  861769973181624320  https://pbs.twimg.com/media/CzG425nWgAAnP7P.jpg   

      img_num             p1   p1_conf  p1_dog           p2   p2_conf  p2_dog  \
1638  2        Arabian_camel  0.366248  False   house_finch  0.209852  False    
1944  2        Arabian_camel  0.366248  False   house_finch  0.209852  False    

                  p3   p3_conf  p3_dog  
1638  cocker_spaniel  0.046403  True    
1944  cocker_spaniel  0.046403  True

In [32]:
# 3 Assess tweet_json data set
tweet_json

tweet_id  followers_count  favourites_count  retweet_count
0     892420643555336193  8848624          145964            7561         
1     892177421306343426  8848624          145964            5603         
2     891815181378084864  8848625          145964            3713         
3     891689557279858688  8848625          145964            7745         
4     891327558926688256  8848625          145964            8339         
5     891087950875897856  8848625          145964            2800         
6     890971913173991426  8848625          145964            1818         
7     890729181411237888  8848625          145964            16919        
8     890609185150312448  8848625          145964            3851         
9     890240255349198849  8848625          145964            6580         
10    890006608113172480  8848625          145964            6570         
11    889880896479866881  8848625          145964            4470         
12    889665388333682689  8848625          145964            8969         
13    889638837579907072  8848625          145964            4014         
14    889531135344209921  8848625          145964            2024         
15    889278841981685760  8848625          145964            4783         
16    888917238123831296  8849373          145964            4023         
17    888804989199671297  8848625          145964            3794         
18    888554962724278272  8848625          145964            3109         
19    888078434458587136  8848625          145964            3115         
20    887705289381826560  8848625          145964            4842         
21    887517139158093824  8848625          145964            10575        
22    887473957103951883  8848625          145964            16134        
23    887343217045368832  8848625          145964            9410         
24    887101392804085760  8848625          145964            5354         
25    886983233522544640  8848625          145964            6864         
26    886736880519319552  8848625          145964            2869         
27    886680336477933568  8848625          145964            4012         
28    886366144734445568  8848625          145964            2838         
29    886267009285017600  8848625          145964            4            
...                  ...      ...             ...           ..            
2301  666411507551481857  8848647          145964            289          
2302  666407126856765440  8848647          145964            32           
2303  666396247373291520  8848647          145964            73           
2304  666373753744588802  8848647          145964            80           
2305  666362758909284353  8848647          145964            509          
2306  666353288456101888  8848647          145964            64           
2307  666345417576210432  8848647          145964            128          
2308  666337882303524864  8848647          145964            82           
2309  666293911632134144  8848647          145964            314          
2310  666287406224695296  8848647          145964            58           
2311  666273097616637952  8848647          145964            70           
2312  666268910803644416  8848647          145964            32           
2313  666104133288665088  8848647          145964            5895         
2314  666102155909144576  8848647          145964            11           
2315  666099513787052032  8848647          145964            58           
2316  666094000022159362  8848647          145964            66           
2317  666082916733198337  8848647          145964            41           
2318  666073100786774016  8848647          145964            143          
2319  666071193221509120  8848647          145964            52           
2320  666063827256086533  8848647          145964            195          
2321  666058600524156928  8848647          145964            52           
2322  666057090499244032  8848647        

In [33]:
tweet_json.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2331 entries, 0 to 2330
Data columns (total 4 columns):
tweet_id            2331 non-null object
followers_count     2331 non-null int64
favourites_count    2331 non-null int64
retweet_count       2331 non-null int64
dtypes: int64(3), object(1)
memory usage: 72.9+ KB


In [34]:
sum(tweet_json.duplicated())

0

quality issues:

twitter_archive:<br>
1-Only keep original ratings (no retweets) that have images. <br>
2-name column: rows 775 and 820 has partially extracted names. <br>
3-name column has incorrectly extracted names like 'a' , 'an', 'the'<br>
4-timestamp has object data type, should be changed to time stamp<br>
5- Tweets have denominator other than 10 have incorrect extracted numerator and denominator  <br>
6- standardize the numerator and denominator ratings by dividing them and provide one value.<br>
7- tweet_id has int type,  should be of type object as no calculation is needed <br>

<br>

image_predictions<br>
8-66 duplicated jpg_url <br>
9-inconsistent capitalization in p1, p2 and p3<br>
10-tweet_id has float type,  should be of type object as no calculation is needed <br>
<br>


tidiness:<br>
1-twitter_archive: remove in_reply_to_status_id, in_reply_to_user_id, retweeted_status_id,retweeted_status_user_id,retweeted_status_timestamp and source <br>
2- image_predictions: dog breed prediction (p1, p2 & p3) and breed prediction confidence (p1_conf, p2_conf, p3_conf) could be combined into pred and pred_conf.<br>
3- combine the three tables  <br>

#### Make copy for each dataset before start cleaning:

In [141]:
twitter_archive_clean = twitter_archive.copy()
image_predictions_clean = image_predictions.copy()


In [142]:
tweet_json_clean= tweet_json.copy()

# Clean:

### Quality

#### Define:<br>
1. Remove Retweets:

In [143]:
# removing all retweets, tweets without images will be removed whem mrging all the tables:

twitter_archive_clean = twitter_archive_clean[pd.isnull(twitter_archive_clean['retweeted_status_user_id'])]

#### Test:<br>

In [144]:
twitter_archive_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2175 entries, 0 to 2355
Data columns (total 17 columns):
tweet_id                      2175 non-null int64
in_reply_to_status_id         78 non-null float64
in_reply_to_user_id           78 non-null float64
timestamp                     2175 non-null object
source                        2175 non-null object
text                          2175 non-null object
retweeted_status_id           0 non-null float64
retweeted_status_user_id      0 non-null float64
retweeted_status_timestamp    0 non-null object
expanded_urls                 2117 non-null object
rating_numerator              2175 non-null int64
rating_denominator            2175 non-null int64
name                          2175 non-null object
doggo                         2175 non-null object
floofer                       2175 non-null object
pupper                        2175 non-null object
puppo                         2175 non-null object
dtypes: float64(4), int64(3), object(1

#### Define:<br>
2. correct manually the names in rows 820 and 775 :

In [145]:
twitter_archive_clean.query('name == "Al"').text

820    Meet Al Cabone. He's a gangsta puppa. Rather h*ckin ruthless. Shows no mercy sometimes. 11/10 pet w extreme caution https://t.co/OUwWbEKOUV
Name: text, dtype: object

#### Code:

In [146]:

twitter_archive_clean.at[775, 'name']= r"O'Malley"
twitter_archive_clean.at[820, 'name']= "Al Cabone"


#### Test:

In [147]:

twitter_archive_clean.query('name == ["Al Cabone" , r"O\'Malley"]')


tweet_id  in_reply_to_status_id  in_reply_to_user_id  \
775  776201521193218049 NaN                    NaN                    
820  770414278348247044 NaN                    NaN                    

                     timestamp  \
775  2016-09-14 23:30:38 +0000   
820  2016-08-30 00:14:12 +0000   

                                                                                 source  \
775  <a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>   
820  <a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>   

                                                                                                                                            text  \
775  This is O'Malley. That is how he sleeps. Doesn't care what you think about it. 10/10 comfy af https://t.co/Pq150LeRaC                         
820  Meet Al Cabone. He's a gangsta puppa. Rather h*ckin ruthless. Shows no mercy sometimes. 11/10 pet w extreme caution https://t.co/OUwWbEKOUV   

     retweeted_status_id  retweeted_status_user_id retweeted_status_timestamp  \
775 NaN                  NaN                        NaN                         
820 NaN                  NaN                        NaN                         

                                                       expanded_urls  \
775  https://twitter.com/dog_rates/status/776201521193218049/photo/1   
820  https://twitter.com/dog_rates/status/770414278348247044/photo/1   

     rating_numerator  rating_denominator       name doggo floofer pupper  \
775  10                10                  O'Malley   None  None    None    
820  11                10                  Al Cabone  None  None    None    

    puppo  
775  None  
820  None

#### Define:<br>
3.  name column has incorrectly extracted names like 'a' , 'an which all are of lower case, these names will be replaced with None:

#### Code:

In [148]:
twitter_archive_clean.name = twitter_archive_clean.name.str.replace('^[a-z]+', "None")


#### Test:

In [149]:

twitter_archive_clean.name.value_counts()
# the value of None increased from 745 to 784

None         784
Charlie      11 
Lucy         11 
Cooper       10 
Oliver       10 
Penny        9  
Tucker       9  
Lola         8  
Winston      8  
Sadie        8  
Toby         7  
Daisy        7  
Stanley      6  
Jax          6  
Bo           6  
Oscar        6  
Bailey       6  
Koda         6  
Bella        6  
Buddy        5  
Dave         5  
Rusty        5  
Chester      5  
Scout        5  
Leo          5  
Milo         5  
Louis        5  
Bentley      5  
Phil         4  
Maggie       4  
            ..  
Ambrose      1  
Timison      1  
Clybe        1  
Darrel       1  
Sierra       1  
Jimbo        1  
Edgar        1  
Rinna        1  
Ozzie        1  
Kenny        1  
Joey         1  
Julio        1  
Acro         1  
Huck         1  
Hurley       1  
Chuq         1  
Clarkus      1  
Koko         1  
Devón        1  
Zuzu         1  
Gidget       1  
Stefan       1  
Bradley      1  
Butter       1  
Tiger        1  
Hector       1  
Alexander    1  
Ronduh       1

#### Define:
4- timestamp to be changed to time stamp data type: 

#### Code:

In [150]:
twitter_archive_clean['timestamp'] = pd.to_datetime(twitter_archive_clean['timestamp'])

#### Test:

In [151]:
twitter_archive_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2175 entries, 0 to 2355
Data columns (total 17 columns):
tweet_id                      2175 non-null int64
in_reply_to_status_id         78 non-null float64
in_reply_to_user_id           78 non-null float64
timestamp                     2175 non-null datetime64[ns]
source                        2175 non-null object
text                          2175 non-null object
retweeted_status_id           0 non-null float64
retweeted_status_user_id      0 non-null float64
retweeted_status_timestamp    0 non-null object
expanded_urls                 2117 non-null object
rating_numerator              2175 non-null int64
rating_denominator            2175 non-null int64
name                          2175 non-null object
doggo                         2175 non-null object
floofer                       2175 non-null object
pupper                        2175 non-null object
puppo                         2175 non-null object
dtypes: datetime64[ns](1), flo

In [152]:
twitter_archive_clean.head()

tweet_id  in_reply_to_status_id  in_reply_to_user_id  \
0  892420643555336193 NaN                    NaN                    
1  892177421306343426 NaN                    NaN                    
2  891815181378084864 NaN                    NaN                    
3  891689557279858688 NaN                    NaN                    
4  891327558926688256 NaN                    NaN                    

            timestamp  \
0 2017-08-01 16:23:56   
1 2017-08-01 00:17:27   
2 2017-07-31 00:18:03   
3 2017-07-30 15:58:51   
4 2017-07-29 16:00:24   

                                                                               source  \
0  <a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>   
1  <a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>   
2  <a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>   
3  <a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>   
4  <a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>   

                                                                                                                                                                 text  \
0  This is Phineas. He's a mystical boy. Only ever appears in the hole of a donut. 13/10 https://t.co/MgUWQ76dJU                                                        
1  This is Tilly. She's just checking pup on you. Hopes you're doing ok. If not, she's available for pats, snugs, boops, the whole bit. 13/10 https://t.co/0Xxu71qeIV   
2  This is Archie. He is a rare Norwegian Pouncing Corgo. Lives in the tall grass. You never know when one may strike. 12/10 https://t.co/wUnZnhtVJB                    
3  This is Darla. She commenced a snooze mid meal. 13/10 happens to the best of us https://t.co/tD36da7qLQ                                                              
4  This is Franklin. He would like you to stop calling him "cute." He is a very fierce shark and should be respected as such. 12/10 #BarkWeek https://t.co/AtUZn91f7f   

   retweeted_status_id  retweeted_status_user_id retweeted_status_timestamp  \
0 NaN                  NaN                        NaN                         
1 NaN                  NaN                        NaN                         
2 NaN                  NaN                        NaN                         
3 NaN                  NaN                        NaN                         
4 NaN                  NaN                        NaN                         

                                                                                                                     expanded_urls  \
0  https://twitter.com/dog_rates/status/892420643555336193/photo/1                                                                   
1  https://twitter.com/dog_rates/status/892177421306343426/photo/1                                                                   
2  https://twitter.com/dog_rates/status/891815181378084864/photo/1                                                                   
3  https://twitter.com/dog_rates/status/891689557279858688/photo/1                                                                   
4  https://twitter.com/dog_rates/status/891327558926688256/photo/1,https://twitter.com/dog_rates/status/891327558926688256/photo/1   

   rating_numerator  rating_denominator      name doggo floofer pupper puppo  
0  13                10                  Phineas   None  None    None   None  
1  13                10                  Tilly     None  None    None   None  
2  12                10                  Archie    None  None    None   None  
3  13                10                  Darla     None  None    None   None  
4  12                10                  Franklin  None  None    None   None

#### Define:
5- Correct the rating numerator and denominator for tweets which has denominator other than 10 and wrong extracted information. <br>
-tweets with index 342, 516 to be removed as there is no rating.<br>



In [153]:
twitter_archive_clean.query('rating_denominator != 10').text

313     @jonnysun @Lin_Manuel ok jomny I know you're excited but 960/00 isn't a valid rating, 13/10 is tho                                                                       
342     @docmisterio account started on 11/15/15                                                                                                                                 
433     The floofs have been released I repeat the floofs have been released. 84/70 https://t.co/NIYC820tmd                                                                      
516     Meet Sam. She smiles 24/7 &amp; secretly aspires to be a reindeer. \nKeep Sam smiling by clicking and sharing this link:\nhttps://t.co/98tB8y7y7t https://t.co/LouL5vdvxx
902     Why does this never happen at my front door... 165/150 https://t.co/HmwrdfEfUE                                                                                           
1068    After so many requests, this is Bretagne. She was the last surviving 9/11 search dog, and our second e

#### Code:

In [154]:
twitter_archive_clean.at[313, 'rating_numerator']=13
twitter_archive_clean.at[313, 'rating_denominator']=10

twitter_archive_clean.at[1068, 'rating_numerator']=14
twitter_archive_clean.at[1068, 'rating_denominator']=10

twitter_archive_clean.at[1165, 'rating_numerator']=13
twitter_archive_clean.at[1165, 'rating_denominator']=10

twitter_archive_clean.at[1202, 'rating_numerator']=11
twitter_archive_clean.at[1202, 'rating_denominator']=10

twitter_archive_clean.at[1662, 'rating_numerator']=10
twitter_archive_clean.at[1662, 'rating_denominator']=10

twitter_archive_clean.at[2335, 'rating_numerator']=9
twitter_archive_clean.at[2335, 'rating_denominator']=10



In [155]:
#tweets with index 342, 516 to be removed as there is no rating.
twitter_archive_clean=twitter_archive_clean.drop([342, 516])

#### Test:

In [156]:
twitter_archive_clean.query('rating_denominator != 10').text

433     The floofs have been released I repeat the floofs have been released. 84/70 https://t.co/NIYC820tmd                                               
902     Why does this never happen at my front door... 165/150 https://t.co/HmwrdfEfUE                                                                    
1120    Say hello to this unbelievably well behaved squad of doggos. 204/170 would try to pet all at once https://t.co/yGQI3He3xv                         
1228    Happy Saturday here's 9 puppers on a bench. 99/90 good work everybody https://t.co/mpvaVxKmc1                                                     
1254    Here's a brigade of puppers. All look very prepared for whatever happens next. 80/80 https://t.co/0eb7R1Om12                                      
1274    From left to right:\nCletus, Jerome, Alejandro, Burp, &amp; Titson\nNone know where camera is. 45/50 would hug all at once https://t.co/sedre1ivTK
1351    Here is a whole flock of puppers.  60/50 I'll take the lot htt

#### Define:
6- divide the numerator by the denominator and add one column for the rating. 

#### Code:

In [157]:
twitter_archive_clean['rating']= twitter_archive_clean['rating_numerator'] / twitter_archive_clean['rating_denominator'].astype(float)

#### Test:

In [158]:
twitter_archive_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2173 entries, 0 to 2355
Data columns (total 18 columns):
tweet_id                      2173 non-null int64
in_reply_to_status_id         77 non-null float64
in_reply_to_user_id           77 non-null float64
timestamp                     2173 non-null datetime64[ns]
source                        2173 non-null object
text                          2173 non-null object
retweeted_status_id           0 non-null float64
retweeted_status_user_id      0 non-null float64
retweeted_status_timestamp    0 non-null object
expanded_urls                 2116 non-null object
rating_numerator              2173 non-null int64
rating_denominator            2173 non-null int64
name                          2173 non-null object
doggo                         2173 non-null object
floofer                       2173 non-null object
pupper                        2173 non-null object
puppo                         2173 non-null object
rating                        

#### Define:
7 and 10- tweet_id has int/float type,  should be of type object as no calculation is needed:

#### Code:

In [159]:
twitter_archive_clean.tweet_id=twitter_archive_clean.tweet_id.astype(str)
image_predictions_clean.tweet_id=image_predictions_clean.tweet_id.astype(str)


#### Test:

In [160]:
twitter_archive_clean.tweet_id.dtypes, image_predictions_clean.tweet_id.dtypes

(dtype('O'), dtype('O'))

#### Define:
8- remove the 66 duplicated jpg_url in image_predictions

#### Code:

In [161]:
image_predictions_clean.drop_duplicates(['jpg_url'], inplace=True)

#### Test:

In [162]:
sum(image_predictions_clean.jpg_url.duplicated())

0

#### Define:
9-change all names to lower case in p1, p2 and p3

#### Code:

In [163]:
image_predictions_clean.p1=image_predictions_clean.p1.str.lower()
image_predictions_clean.p2=image_predictions_clean.p2.str.lower()
image_predictions_clean.p3=image_predictions_clean.p3.str.lower()


#### Test:

In [164]:
image_predictions_clean.head()

tweet_id                                          jpg_url  \
0  666020888022790149  https://pbs.twimg.com/media/CT4udn0WwAA0aMy.jpg   
1  666029285002620928  https://pbs.twimg.com/media/CT42GRgUYAA5iDo.jpg   
2  666033412701032449  https://pbs.twimg.com/media/CT4521TWwAEvMyu.jpg   
3  666044226329800704  https://pbs.twimg.com/media/CT5Dr8HUEAA-lEu.jpg   
4  666049248165822465  https://pbs.twimg.com/media/CT5IQmsXIAAKY4A.jpg   

   img_num                      p1   p1_conf  p1_dog                  p2  \
0  1        welsh_springer_spaniel  0.465074  True    collie               
1  1        redbone                 0.506826  True    miniature_pinscher   
2  1        german_shepherd         0.596461  True    malinois             
3  1        rhodesian_ridgeback     0.408143  True    redbone              
4  1        miniature_pinscher      0.560311  True    rottweiler           

    p2_conf  p2_dog                   p3   p3_conf  p3_dog  
0  0.156665  True    shetland_sheepdog    0.061428  True    
1  0.074192  True    rhodesian_ridgeback  0.072010  True    
2  0.138584  True    bloodhound           0.116197  True    
3  0.360687  True    miniature_pinscher   0.222752  True    
4  0.243682  True    doberman             0.154629  True

### Tidiness

#### Define:
1-twitter_archive: remove columns which are not providing information about dogs/ratings which are: in_reply_to_status_id, in_reply_to_user_id, retweeted_status_id,retweeted_status_user_id,retweeted_status_timestamp, expanded_url and source <br>

#### Code:

In [165]:
twitter_archive_clean.drop(['in_reply_to_status_id', 'in_reply_to_user_id','retweeted_status_id', 'retweeted_status_user_id', 'retweeted_status_timestamp','expanded_urls', 'source'], axis = 1, inplace = True)

#### Test:

In [166]:
twitter_archive_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2173 entries, 0 to 2355
Data columns (total 11 columns):
tweet_id              2173 non-null object
timestamp             2173 non-null datetime64[ns]
text                  2173 non-null object
rating_numerator      2173 non-null int64
rating_denominator    2173 non-null int64
name                  2173 non-null object
doggo                 2173 non-null object
floofer               2173 non-null object
pupper                2173 non-null object
puppo                 2173 non-null object
rating                2173 non-null float64
dtypes: datetime64[ns](1), float64(1), int64(2), object(7)
memory usage: 203.7+ KB


#### Define: 
2- image_predictions: dog breed predictions (p1, p2 & p3) to be combined in one column (pred) and breed predictions confidence (p1_conf, p2_conf, p3_conf) to be combined into (pred_conf) column. drop (p1, p2 & p3, p1_conf, p2_conf, p3_conf) columns after combining them.check if there is any missing values in the new list and drop the NaN <br>

In [167]:
 image_predictions_clean.head(20)

tweet_id                                          jpg_url  \
0   666020888022790149  https://pbs.twimg.com/media/CT4udn0WwAA0aMy.jpg   
1   666029285002620928  https://pbs.twimg.com/media/CT42GRgUYAA5iDo.jpg   
2   666033412701032449  https://pbs.twimg.com/media/CT4521TWwAEvMyu.jpg   
3   666044226329800704  https://pbs.twimg.com/media/CT5Dr8HUEAA-lEu.jpg   
4   666049248165822465  https://pbs.twimg.com/media/CT5IQmsXIAAKY4A.jpg   
5   666050758794694657  https://pbs.twimg.com/media/CT5Jof1WUAEuVxN.jpg   
6   666051853826850816  https://pbs.twimg.com/media/CT5KoJ1WoAAJash.jpg   
7   666055525042405380  https://pbs.twimg.com/media/CT5N9tpXIAAifs1.jpg   
8   666057090499244032  https://pbs.twimg.com/media/CT5PY90WoAAQGLo.jpg   
9   666058600524156928  https://pbs.twimg.com/media/CT5Qw94XAAA_2dP.jpg   
10  666063827256086533  https://pbs.twimg.com/media/CT5Vg_wXIAAXfnj.jpg   
11  666071193221509120  https://pbs.twimg.com/media/CT5cN_3WEAAlOoZ.jpg   
12  666073100786774016  https://pbs.twimg.com/media/CT5d9DZXAAALcwe.jpg   
13  666082916733198337  https://pbs.twimg.com/media/CT5m4VGWEAAtKc8.jpg   
14  666094000022159362  https://pbs.twimg.com/media/CT5w9gUW4AAsBNN.jpg   
15  666099513787052032  https://pbs.twimg.com/media/CT51-JJUEAA6hV8.jpg   
16  666102155909144576  https://pbs.twimg.com/media/CT54YGiWUAEZnoK.jpg   
17  666104133288665088  https://pbs.twimg.com/media/CT56LSZWoAAlJj2.jpg   
18  666268910803644416  https://pbs.twimg.com/media/CT8QCd1WEAADXws.jpg   
19  666273097616637952  https://pbs.twimg.com/media/CT8T1mtUwAA3aqm.jpg   

    img_num                      p1   p1_conf  p1_dog                  p2  \
0   1        welsh_springer_spaniel  0.465074  True    collie               
1   1        redbone                 0.506826  True    miniature_pinscher   
2   1        german_shepherd         0.596461  True    malinois             
3   1        rhodesian_ridgeback     0.408143  True    redbone              
4   1        miniature_pinscher      0.560311  True    rottweiler           
5   1        bernese_mountain_dog    0.651137  True    english_springer     
6   1        box_turtle              0.933012  False   mud_turtle           
7   1        chow                    0.692517  True    tibetan_mastiff      
8   1        shopping_cart           0.962465  False   shopping_basket      
9   1        miniature_poodle        0.201493  True    komondor             
10  1        golden_retriever        0.775930  True    tibetan_mastiff      
11  1        gordon_setter           0.503672  True    yorkshire_terrier    
12  1        walker_hound            0.260857  True    english_foxhound     
13  1        pug                     0.489814  True    bull_mastiff         
14  1        bloodhound              0.195217  True    german_shepherd      
15  1        lhasa                   0.582330  True    shih-tzu             
16  1        english_setter          0.298617  True    newfoundland         
17  1        hen                     0.965932  False   cock                 
18  1        desktop_computer        0.086502  False   desk                 
19  1        italian_greyhound       0.176053  True    toy_terrier          

     p2_conf  p2_dog                           p3   p3_conf  p3_dog  
0   0.156665  True    shetland_sheepdog            0.061428  True    
1   0.074192  True    rhodesian_ridgeback          0.072010  True    
2   0.138584  True    bloodhound                   0.116197  True    
3   0.360687  True    miniature_pinscher           0.222752  True    
4   0.243682  True    doberman                     0.154629  True    
5   0.263788  True    greater_swiss_mountain_dog   0.016199  True    
6   0.045885  False   terrapin                     0.017885  False   
7   0.058279  True    fur_coat                     0.054449  False   
8   0.014594  False   golden_retriever             0.007959  True    
9   0.192305  True    soft-coated_wheaten_terrier  0.082086  True    
10  0.093718  True    labrador_retriever          

In [168]:
pred=[]
pred_conf=[]
for i in  image_predictions_clean.index:
    if image_predictions_clean.p1_dog[i]== True:
        pred.append(image_predictions_clean.p1[i])
        pred_conf.append(image_predictions_clean.p1_conf[i])
            
    elif image_predictions_clean.p2_dog[i]== True:
        pred.append(image_predictions_clean.p2[i])
        pred_conf.append(image_predictions_clean.p2_conf[i])
        
    elif image_predictions_clean.p3_dog[i]== True:
        pred.append(image_predictions_clean.p3[i])
        pred_conf.append(image_predictions_clean.p3_conf[i])
        
    else:
        pred.append(np.NaN)
        pred_conf.append(np.NaN)
        
image_predictions_clean['pred']=pred
image_predictions_clean['pred_conf']=pred_conf 
        

In [169]:
# drop columns 'p1', 'p1_conf', 'p1_dog', 'p2', 'p2_conf', 'p2_dog', 'p3', 'p3_conf', 'p3_dog'
columns= ['p1','p1_conf','p1_dog','p2','p2_conf','p2_dog','p3','p3_conf','p3_dog']
image_predictions_clean.drop(columns, axis =1, inplace=True)

In [170]:
image_predictions_clean.head()

tweet_id                                          jpg_url  \
0  666020888022790149  https://pbs.twimg.com/media/CT4udn0WwAA0aMy.jpg   
1  666029285002620928  https://pbs.twimg.com/media/CT42GRgUYAA5iDo.jpg   
2  666033412701032449  https://pbs.twimg.com/media/CT4521TWwAEvMyu.jpg   
3  666044226329800704  https://pbs.twimg.com/media/CT5Dr8HUEAA-lEu.jpg   
4  666049248165822465  https://pbs.twimg.com/media/CT5IQmsXIAAKY4A.jpg   

   img_num                    pred  pred_conf  
0  1        welsh_springer_spaniel  0.465074   
1  1        redbone                 0.506826   
2  1        german_shepherd         0.596461   
3  1        rhodesian_ridgeback     0.408143   
4  1        miniature_pinscher      0.560311

In [171]:
# check if there is any missing value after the combination
image_predictions_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2009 entries, 0 to 2074
Data columns (total 5 columns):
tweet_id     2009 non-null object
jpg_url      2009 non-null object
img_num      2009 non-null int64
pred         1691 non-null object
pred_conf    1691 non-null float64
dtypes: float64(1), int64(1), object(3)
memory usage: 174.2+ KB


In [172]:
# drop nan
image_predictions_clean.dropna(inplace=True);

In [173]:
# test that the rows with nan are dropped
image_predictions_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1691 entries, 0 to 2073
Data columns (total 5 columns):
tweet_id     1691 non-null object
jpg_url      1691 non-null object
img_num      1691 non-null int64
pred         1691 non-null object
pred_conf    1691 non-null float64
dtypes: float64(1), int64(1), object(3)
memory usage: 79.3+ KB


#### Define:
10- Combine the three datasets into one dataset:

In [174]:
#to combine image_predictions_clean and tweet_json_clean we need to set the tweet_id column to be the index
image_predictions_clean.set_index('tweet_id', inplace = True)
tweet_json_clean.set_index('tweet_id', inplace = True)

In [182]:
df1 = pd.merge(left=twitter_archive_clean, right=image_predictions_clean, how='left',on= ['tweet_id'])
df = pd.merge(left=df1, right=tweet_json_clean, how='left',on= ['tweet_id'])

In [183]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2173 entries, 0 to 2172
Data columns (total 18 columns):
tweet_id              2173 non-null object
timestamp             2173 non-null datetime64[ns]
text                  2173 non-null object
rating_numerator      2173 non-null int64
rating_denominator    2173 non-null int64
name                  2173 non-null object
doggo                 2173 non-null object
floofer               2173 non-null object
pupper                2173 non-null object
puppo                 2173 non-null object
rating                2173 non-null float64
jpg_url               1685 non-null object
img_num               1685 non-null float64
pred                  1685 non-null object
pred_conf             1685 non-null float64
followers_count       2166 non-null float64
favourites_count      2166 non-null float64
retweet_count         2166 non-null float64
dtypes: datetime64[ns](1), float64(6), int64(2), object(9)
memory usage: 322.6+ KB


In [185]:
# drop tweets wihout images  (jpg_url is null)
df.dropna(inplace= True)


In [186]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1678 entries, 1 to 2172
Data columns (total 18 columns):
tweet_id              1678 non-null object
timestamp             1678 non-null datetime64[ns]
text                  1678 non-null object
rating_numerator      1678 non-null int64
rating_denominator    1678 non-null int64
name                  1678 non-null object
doggo                 1678 non-null object
floofer               1678 non-null object
pupper                1678 non-null object
puppo                 1678 non-null object
rating                1678 non-null float64
jpg_url               1678 non-null object
img_num               1678 non-null float64
pred                  1678 non-null object
pred_conf             1678 non-null float64
followers_count       1678 non-null float64
favourites_count      1678 non-null float64
retweet_count         1678 non-null float64
dtypes: datetime64[ns](1), float64(6), int64(2), object(9)
memory usage: 249.1+ KB
